importing relevant packages

In [1]:
import pandas as pd
import os
import glob
import pandas_profiling
from pandas_profiling.utils.cache import cache_file

creating path to folder and a variable called all_files that globs all files in that path ending in .csv

In [2]:
path = r'C:\Users\colem\OneDrive\Documents\Springboard\COVID-19-master\csse_covid_19_data\csse_covid_19_daily_reports_us'
all_files = glob.glob(path + '*/*.csv')

creating empty list to hold csvs previously read. Filling list with all the csv files in all_files

In [3]:
csv_list = []
for csv_name in all_files:
    csv_df = pd.read_csv(csv_name, index_col=None, header = 0)
    csv_list.append(csv_df)

converting csv_list to dataFrame containing all data

In [4]:
df = pd.concat(csv_list, axis = 0, ignore_index=True)

removing all data except North Carolina covid data

In [5]:
NC_df = df[df['Province_State'] == 'North Carolina']

As project was originally supposed to be on one years worth of data, segmented data to March 1st 2021 to Feburary 28th 2022

In [6]:
NC_df_dated = NC_df[(NC_df['Last_Update'] >= '2021-03-01') & (NC_df['Last_Update'] <= '2022-02-28')]
NC_df_dated.head()

Province_State Country_Region          Last_Update      Lat    Long_  \
95   North Carolina             US  2022-01-02 04:32:57  35.6301 -79.8064   
211  North Carolina             US  2022-01-03 02:33:49  35.6301 -79.8064   
327  North Carolina             US  2022-01-04 04:33:16  35.6301 -79.8064   
443  North Carolina             US  2022-01-05 04:33:14  35.6301 -79.8064   
559  North Carolina             US  2022-01-06 04:33:48  35.6301 -79.8064   

     Confirmed  Deaths  Recovered  Active  FIPS  Incident_Rate  \
95     1686667   19426        NaN     NaN  37.0   16081.745722   
211    1686667   19426        NaN     NaN  37.0   16081.745722   
327    1732568   19457        NaN     NaN  37.0   16519.394772   
443    1742844   19494        NaN     NaN  37.0   16617.372630   
559    1763614   19542        NaN     NaN  37.0   16815.406894   

     Total_Test_Results  People_Hospitalized  Case_Fatality_Ratio         UID  \
95           18909822.0                  NaN             1.151739  84000037.0   
211          18909822.0                  NaN             1.151739  84000037.0   
327          18909822.0                  NaN             1.123015  84000037.0   
443          19173118.0                  NaN             1.118517  84000037.0   
559          19208772.0                  NaN             1.108066  84000037.0   

    ISO3   Testing_Rate  Hospitalization_Rate  People_Tested  Mortality_Rate  
95   USA  180298.155507                   NaN            NaN             NaN  
211  USA  180298.155507                   NaN            NaN             NaN  
327  USA  180298.155507                   NaN            NaN             NaN  
443  USA  182808.585438                   NaN            NaN             NaN  
559  USA  183148.533135                   NaN            NaN             NaN

created variable 'missing' to check null values and ran a percentage of those values versus total values. Checked NC_df_dated first. Learned that 100% of 6 columns were missing (Mortality_Rate, People_Tested, Hospitalization_Rate, Recovered, Active, People_Hospitalized)

In [7]:
missing = pd.DataFrame([NC_df_dated.isnull().sum(),100 * NC_df_dated.isnull().mean()]).T
missing_sorted = missing.sort_values(by = [0], ascending = False)
missing_sorted.columns = ['Count','%']
missing_sorted

Count      %
Mortality_Rate        364.0  100.0
People_Tested         364.0  100.0
Hospitalization_Rate  364.0  100.0
Recovered             364.0  100.0
Active                364.0  100.0
People_Hospitalized   364.0  100.0
Total_Test_Results      0.0    0.0
Testing_Rate            0.0    0.0
ISO3                    0.0    0.0
UID                     0.0    0.0
Case_Fatality_Ratio     0.0    0.0
Province_State          0.0    0.0
Country_Region          0.0    0.0
FIPS                    0.0    0.0
Deaths                  0.0    0.0
Confirmed               0.0    0.0
Long_                   0.0    0.0
Lat                     0.0    0.0
Last_Update             0.0    0.0
Incident_Rate           0.0    0.0

after learning that multiple values were missing in their entirety in NC_df_dated decided to check if that was the case for all of the NC data. As it was not decided to change the scope of the project to include all NC data

In [8]:
missing = pd.DataFrame([NC_df.isnull().sum(),100 * NC_df.isnull().mean()]).T
missing_sorted = missing.sort_values(by = [0], ascending = False)
missing_sorted.columns = ['Count','%']
missing_sorted

Count          %
Hospitalization_Rate  712.0  97.802198
People_Hospitalized   712.0  97.802198
Mortality_Rate        517.0  71.016484
People_Tested         517.0  71.016484
Recovered             435.0  59.752747
Active                435.0  59.752747
Total_Test_Results    211.0  28.983516
Case_Fatality_Ratio   211.0  28.983516
Testing_Rate            0.0   0.000000
ISO3                    0.0   0.000000
UID                     0.0   0.000000
Province_State          0.0   0.000000
Country_Region          0.0   0.000000
FIPS                    0.0   0.000000
Deaths                  0.0   0.000000
Confirmed               0.0   0.000000
Long_                   0.0   0.000000
Lat                     0.0   0.000000
Last_Update             0.0   0.000000
Incident_Rate           0.0   0.000000

checking data types of all columns. Determined Last_Update should be changed to Date/Time. Province_State should be string. Country_Region should be string. ISO3 should be string. Total_Test_Results, Recovered, Active, People_Hospitalized, People_Tested should all be ints however should ignore null values.

In [9]:
NC_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 728 entries, 37 to 42221
Data columns (total 20 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Province_State        728 non-null    object 
 1   Country_Region        728 non-null    object 
 2   Last_Update           728 non-null    object 
 3   Lat                   728 non-null    float64
 4   Long_                 728 non-null    float64
 5   Confirmed             728 non-null    int64  
 6   Deaths                728 non-null    int64  
 7   Recovered             293 non-null    float64
 8   Active                293 non-null    float64
 9   FIPS                  728 non-null    float64
 10  Incident_Rate         728 non-null    float64
 11  Total_Test_Results    517 non-null    float64
 12  People_Hospitalized   16 non-null     float64
 13  Case_Fatality_Ratio   517 non-null    float64
 14  UID                   728 non-null    float64
 15  ISO3                

Changing datatypes of those listed above to correct datatype. Confirmed changes occured correctly after

In [10]:
NC_df['Last_Update']= pd.to_datetime(NC_df['Last_Update'])
NC_df[['Province_State', 'Country_Region', 'ISO3']] = NC_df[['Province_State', 'Country_Region', 'ISO3']].astype('string') 
NC_df[['Total_Test_Results', 'Recovered', 'Active', 'People_Hospitalized', 'People_Tested']] = NC_df [['Total_Test_Results', 'Recovered', 'Active', 'People_Hospitalized', 'People_Tested']].astype('Int64')
NC_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 728 entries, 37 to 42221
Data columns (total 20 columns):
 #   Column                Non-Null Count  Dtype         
---  ------                --------------  -----         
 0   Province_State        728 non-null    string        
 1   Country_Region        728 non-null    string        
 2   Last_Update           728 non-null    datetime64[ns]
 3   Lat                   728 non-null    float64       
 4   Long_                 728 non-null    float64       
 5   Confirmed             728 non-null    int64         
 6   Deaths                728 non-null    int64         
 7   Recovered             293 non-null    Int64         
 8   Active                293 non-null    Int64         
 9   FIPS                  728 non-null    float64       
 10  Incident_Rate         728 non-null    float64       
 11  Total_Test_Results    517 non-null    Int64         
 12  People_Hospitalized   16 non-null     Int64         
 13  Case_Fatality_Rat

C:\Users\colem\anaconda3\envs\Springboard\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
C:\Users\colem\anaconda3\envs\Springboard\lib\site-packages\pandas\core\frame.py:3065: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[k1] = value[k2]


Looking for columns that have only one unique value and thus can be erased. Decided to keep Province_State but remove all other columns with only one unique value.

In [11]:
NC_df.nunique()

Province_State            1
Country_Region            1
Last_Update             728
Lat                       1
Long_                     1
Confirmed               596
Deaths                  594
Recovered                42
Active                  285
FIPS                      1
Incident_Rate           596
Total_Test_Results      385
People_Hospitalized      16
Case_Fatality_Ratio     385
UID                       1
ISO3                      1
Testing_Rate            596
Hospitalization_Rate     16
People_Tested           211
Mortality_Rate          211
dtype: int64

Dropping non-relevant columns with no unique information

In [12]:
NC_df = NC_df.drop(['Country_Region', 'Lat', 'Long_', 'FIPS', 'UID', 'ISO3'], 1)

In [13]:
NC_df.describe()

Confirmed        Deaths      Recovered         Active  \
count  7.280000e+02    728.000000     293.000000     293.000000   
mean   9.484120e+05  10926.200549  240427.866894   42962.795222   
std    7.622404e+05   7140.562261  211827.207366   34375.972170   
min    4.570000e+03     89.000000       0.000000    5584.000000   
25%    2.310412e+05   3768.750000   67124.000000   19815.000000   
50%    9.294060e+05  12248.000000  184422.000000   27486.000000   
75%    1.425062e+06  17104.000000  341041.000000   60374.000000   
max    2.634007e+06  23257.000000  795521.000000  154526.000000   

       Incident_Rate  Total_Test_Results  People_Hospitalized  \
count     728.000000        5.170000e+02            16.000000   
mean     9042.757699        1.386199e+07           425.250000   
std      7267.680423        5.097243e+06            50.552283   
min        43.573259        4.399616e+06           313.000000   
25%      2202.892826        1.026146e+07           410.500000   
50%      8861.542299        1.277368e+07           432.500000   
75%     13587.438850        1.775051e+07           458.250000   
max     25114.282075        2.287576e+07           486.000000   

       Case_Fatality_Ratio   Testing_Rate  Hospitalization_Rate  \
count           517.000000     728.000000             16.000000   
mean              1.207252   98525.063272              6.410531   
std               0.165593   67058.785147              1.079725   
min               0.851899     626.535422              5.012782   
25%               1.185888   32216.477767              5.667870   
50%               1.227974  102645.640519              6.173156   
75%               1.312974  153027.016183              7.133303   
max               1.566692  218111.868669              8.175240   

       People_Tested  Mortality_Rate  
count   2.110000e+02      211.000000  
mean    1.686436e+06        2.213960  
std     1.283329e+06        0.797946  
min     6.213900e+04        1.570538  
25%     4.587825e+05        1.627175  
50%     1.613385e+06        1.677428  
75%     2.698780e+06        2.859806  
max     4.365061e+06        3.840737

resetting index as it was mixed from when other states were dropped

In [14]:
NC_df = NC_df.reset_index(drop=True)

Running a Pandas Profiling non exploratory report 

In [15]:
report = NC_df.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report

running an exploratory Pandas Profiling report

In [16]:
profile_report = NC_df.profile_report(explorative=True, html={'style': {'full_width': True}})
profile_report

For this Notebook I read in all the CSV files with COVID data from the US Daily Reports. My goal was to visualize one years worth of North Carolina data. After segmenting North Carolina and ones years worth of data I checked the null values and realized that 6 columns were completely missing for that year. After that discovery I decided to expand the scope of the project to include all the data received for North Carolina as those null columns were included in older data. I adjusted that data types to the correct types for each column and removed any column with a repeating nonunique single value as they weren't providing any information we didn't already know. I then ran the data through pandas profiling in a explorative and non-explorative format.